In [1]:
from huggingface_hub import snapshot_download
data_folder = snapshot_download("fxtentacle/tevr-token-entropy-predictor-de")

In [2]:
from transformers import T5ForConditionalGeneration
model = T5ForConditionalGeneration.from_pretrained(data_folder)
model.to('cuda')
model.eval()
None

In [3]:
import torch

def text_to_cross_entropy(text):
    ttext = torch.tensor([[0]+list(text.encode('UTF-8'))],dtype=torch.int64).to('cuda')
    tone = torch.tensor([[1]],dtype=torch.int32).to('cuda')
    logits = model.forward(input_ids=tone, attention_mask=tone, decoder_input_ids=ttext, return_dict=False)[0].detach()
    cross_entropy = torch.nn.functional.cross_entropy(input=logits[0][:-1], target=ttext[0][1:], reduction='none').detach().cpu().numpy()
    return cross_entropy

In [4]:
import sys
import os
sys.path.append(data_folder)
from text_tokenizer import HajoTextTokenizer

In [5]:
tokenizer_file = 'text-tokenizer-de-4m.txt'
text_tokenizer = HajoTextTokenizer(data_folder+'/'+tokenizer_file)

In [6]:
text = "die katze ist niedlich"
cross_entropy = text_to_cross_entropy(text)

tokens = text_tokenizer.encode(text)
tokens = [text_tokenizer.all_tokens[t] for t in tokens]
print(tokens)
token_sums = []
token_sums2 = []
for t in tokens:
    ce = sum(cross_entropy[len(token_sums):len(token_sums)+len(t)])
    for r in range(len(t)): token_sums.append(ce  / len(t))
    token_sums2.append(ce)
print(token_sums)

['die', ' ', 'k', 'at', 'ze', ' ', 'ist', ' ', 'n', 'ied', 'lich']
[3.3762913048267365, 3.3762913048267365, 3.3762913048267365, 0.29695791006088257, 4.193424224853516, 2.3430762887001038, 2.3430762887001038, 2.8417416363954544, 2.8417416363954544, 1.1227068901062012, 2.017452405144771, 2.017452405144771, 2.017452405144771, 0.0016304069431498647, 2.580254554748535, 2.3091587026913962, 2.3091587026913962, 2.3091587026913962, 1.0126478232632508, 1.0126478232632508, 1.0126478232632508, 1.0126478232632508]


In [7]:
import numpy as np
html = '<table style="font-size: 20px; font-family: Roboto">'
html += '<tr><td><b>(1)</b></td>'+''.join([f'<td style="text-align:left">{c}</td>' for c in list(text)])+'</tr>'
html += '<tr><td><b>(2)</b></td>'+''.join(['<td>1.0</td>'.format(v) for v in cross_entropy])+'<td>σ²={:3.1f}</td>'.format(np.var([1.0 for v in cross_entropy]))+'</tr>'
html += '<tr><td><b>(3)</b></td>'+''.join(['<td>{:3.1f}</td>'.format(v) for v in cross_entropy])+'<td>σ²={:3.1f}</td>'.format(np.var(cross_entropy))+'</tr>'
html += '<tr><td><b>(4)</b></td>'+''.join([f'<td style="text-align:center" colspan={len(t)}>{t}</td>' for t in tokens])+'</tr>'
html += '<tr><td><b>(5)</b></td>'+''.join([f'<td style="text-align:center" colspan={len(t)}>{"{:3.1f}".format(token_sums2[i])}</td>' for i,t in enumerate(tokens)])+'</tr>'
html += '<tr><td><b>(6)</b></td>'+''.join(['<td>{:3.1f}</td>'.format(v) for v in token_sums])+'<td>σ²={:3.1f}</td>'.format(np.var(token_sums))+'</tr>'
html += '</table>'

import IPython
IPython.display.HTML(html)

In [8]:
from text_tokenizer import HajoTextTokenizer
text_tokenizer = HajoTextTokenizer(data_folder+'/'+tokenizer_file)
tt = text_tokenizer.all_tokens
print(', '.join(tt))

<pad>, <eos>,  , chen, sche, lich, isch, icht, iche, eine, rden, tion, urde, haft, eich, rung, chte, ssen, chaf, nder, tlic, tung, eite, iert, sich, ngen, erde, scha, nden, unge, lung, mmen, eren, ende, inde, erun, sten, iese, igen, erte, iner, tsch, keit, der, die, ter, und, ein, ist, den, ten, ber, ver, sch, ung, ste, ent, ach, nte, auf, ben, eit, des, ers, aus, das, von, ren, gen, nen, lle, hre, mit, iel, uch, lte, ann, lie, men, dem, and, ind, als, sta, elt, ges, tte, ern, wir, ell, war, ere, rch, abe, len, ige, ied, ger, nnt, wei, ele, och, sse, end, all, ahr, bei, sie, ede, ion, ieg, ege, auc, che, rie, eis, vor, her, ang, für, ass, uss, tel, er, in, ge, en, st, ie, an, te, be, re, zu, ar, es, ra, al, or, ch, et, ei, un, le, rt, se, is, ha, we, at, me, ne, ur, he, au, ro, ti, li, ri, eh, im, ma, tr, ig, el, um, la, am, de, so, ol, tz, il, on, it, sc, sp, ko, na, pr, ni, si, fe, wi, ns, ke, ut, da, gr, eu, mi, hr, ze, hi, ta, ss, ng, sa, us, ba, ck, em, kt, ka, ve, fr, bi, wa, ah,